In [ ]:
using MathOptInterface
const MOI = MathOptInterface
using Convex, ECOS
using LinearAlgebra

In [ ]:
m_wet = 2000.0 # rocket wet mass [kg]
m_dry =  300.0 # rocket dry mass [kg]
thrust_max = 24000.0 # maximum thrust
ρ1 = 0.2 * thrust_max # lower bound on thrust
ρ2 = 0.8 * thrust_max # upper bound on thrust
α = 5e-4 # rocket specific impulse [s]
θ = deg2rad(30) # max thrust angle deviation from vertical [rad]
γ = deg2rad(15) # angle, measured from the horizontal, that defines the no-fly bounds [rad]
g = 3.71 # gravity [m/s2]
tf = 52.0 # duration of the simulation [s]
n = 50 # number of points used in the descritization of time [-]

In [ ]:
# derived parameters
t = collect(range(0, tf, n)) # time vector [s]
dt = t[2] - t[1]

In [ ]:
# initial conditions
x0 = [600.0, 1200.0, 50.0, -95.0, log(m_wet)] # initial state (x,y,x_dot,y_dot,z)

In [ ]:
Ac = vcat(
        hcat(zeros(2,2), Matrix(1.0I, 2, 2), zeros(2,1)),
        hcat(zeros(2,2), zeros(2,2),         zeros(2,1)),
        zeros(1,5)
     )
Ad = exp(Ac.*dt)

In [ ]:
function integrate_trapezoidal(f, a, b, n)
    b > a || @error("a must be less than b")
    n > 1 || @error("n must be positive")
    
    retval = f(a)./2 + f(b)./2
    for k in 1 : n-1
        retval = retval + f(a + k*(b-a)/n)
    end
    retval *= (b - a)/ n
    return retval
end

Bc = vcat(
        hcat(zeros(2,2),         zeros(2,1)),
        hcat(Matrix(1.0I, 2, 2), zeros(2,1)),
        hcat(zeros(1,2),         -α)
    )
Bd1 = integrate_trapezoidal(s -> exp(Ac.*(dt-s))*Bc, 0.0, dt, 10000)
Bd2 = integrate_trapezoidal(s -> exp(Ac.*(dt-s))*Bc*s/dt, 0.0, dt, 10000)

In [ ]:
g3 = [0.0, -g, 0.0] # gravitational 3-vector [m/s2]

function get_xk(Ad, Bd1, Bd2, η, x0, g3, k)
    xk = copy(x0)
    p_km1 = [0.0,0.0,0.0]
    p_k = η[1:3]
    ind_low = 1
    for j in 1:k
        xk = Ad*xk + Bd1*(p_km1 + g3) + Bd2*(p_k - p_km1)
        p_km1 = p_k
        ind_low = min(ind_low +3, length(η)-2)
        p_k = η[ind_low : ind_low+2]
    end
    return xk
end

In [ ]:
# Create the convex.jl problem
η = Variable(3n) # for our n control points
ω = repeat([0,0,1], outer = [n]) # only minimize σ's

# minimize fuel consumption
problem = minimize(ω⋅η)

println("thrust magnitude constraints")
for k in 1:n
    j = 3*(k-1)+1
    problem.constraints += norm(η[j:j+1]) <= η[j+2]
end

# println("thrust cant angle constraints")
for k in 1:n
    j = 3*(k-1)+1
    uy = η[j+1]
    σ = η[j+2]
    problem.constraints += uy >= cos(θ) * σ
end

println("thrust slack variable lower and upper bounds")
z0 = k -> log(m_wet - α*ρ2*dt*k)
for k in 1:n
    j = 3*(k-1)+1
    σk = η[j+2]
    xk = get_xk(Ad, Bd1, Bd2, η, x0, g3, k)
    zk = xk[end]
    problem.constraints += ρ1 * exp(-z0(k)) * (1 - (zk-z0(k)) + 0.5*(zk*zk -2*z0(k)*zk + z0(k)*z0(k))) <= σk
    problem.constraints += σk <= ρ2 * exp(-z0(k)) * (1 - (zk-z0(k)))
end

println("glide angle constraints")
for k in 1:n
    xk = get_xk(Ad, Bd1, Bd2, η, x0, g3, k)
    problem.constraints += xk[2] >= tan(γ) * xk[1]
end

println("terminal conditions")
xend = get_xk(Ad, Bd1, Bd2, η, x0, g3, n)
problem.constraints += xend[1:4] == [0,0,0,0]
problem.constraints += xend[5] >= log(m_dry)


nothing

In [ ]:
optimizer = ECOS.Optimizer()
solve!(problem, optimizer; silent_solver = false)

In [ ]:
problem.status

In [ ]:
problem.optval

In [ ]:
# extract a solution
η_eval = evaluate(η)

xk = Array{Float64}(undef, length(x0), length(t))
for k in 1 : n
    xk[:,k] = get_xk(Ad, Bd1, Bd2, η_eval, x0, g3, k)
end

xs = xk[1,:]
ys = xk[2,:]
us = xk[3,:]
vs = xk[4,:]
zs = xk[5,:]

mass = exp.(zs)

u1 = η_eval[1:3:end]
u2 = η_eval[2:3:end]
σ = η_eval[3:3:end]
Tx = u1 .* mass
Ty = u2 .* mass
Γ = σ .* mass
thrust_mag = [hypot(Tyi, Txi) for (Txi, Tyi) in zip(Tx, Ty)]
thrust_ang = [atan(Tyi, Txi) for (Txi, Tyi) in zip(Tx, Ty)]

nothing

In [ ]:
using PGFPlots

Axis([
        Plots.Linear(t, Tx, style="solid, thick, blue, mark=none", legendentry="Tx"),
        Plots.Linear(t, Ty, style="solid, thick, red, mark=none", legendentry="Ty"),
     ], xlabel="time [s]", ylabel="thrust", style="width=15cm, height=8cm, legend pos=outer north east")

In [ ]:
σ_lowerbound = [ρ1 * exp(-z0(k)) * (1 - (zs[k]-z0(k)) + 0.5*(zs[k] -z0(k))^2) for k in 1:n]
σ_upperbound = [ρ2 * exp(-z0(k)) * (1 - (zs[k]-z0(k))) for k in 1:n]

Axis([
        Plots.Linear(t, σ, style="solid, thick, purple, mark=none"),
        Plots.Linear(t, σ_lowerbound, style="solid, black, mark=none"),
        Plots.Linear(t, σ_upperbound, style="solid, black, mark=none")
     ], xlabel="time [s]", ylabel="sigma", style="width=15cm, height=8cm")

In [ ]:
Axis(
    [
        Plots.Linear([t[1], t[end]], [ρ1, ρ1], style="solid, thick, black, mark=none", legendentry="upperbound"),
        Plots.Linear([t[1], t[end]], [ρ2, ρ2], style="solid, thick, black, mark=none", legendentry="lowerbound"),
        Plots.Linear(t[2:end-1], thrust_mag[2:end-1], style="solid, thick, red, mark=none", legendentry="norm(T)"),
        Plots.Linear(t[2:end-1], Γ[2:end-1], style="solid, thick, gray, mark=none", legendentry="Gamma"),
    ], xlabel="time [s]", ylabel="thrust magnitude [N]", style="width=15cm, height=8cm, ymin=0, legend pos=outer north east")

In [ ]:
Axis(
    [
        Plots.Linear([t[1], t[end]], [m_wet, m_wet], style="solid, thick, black, mark=none", legendentry="wet mass"),
        Plots.Linear([t[1], t[end]], [m_dry, m_dry], style="solid, thick, black, mark=none", legendentry="dry mass"),
        Plots.Linear(t, mass, style="solid, thick, red, mark=none", legendentry="mass"),
    ], xlabel="time [s]", ylabel="mass [kg]", style="width=15cm, height=8cm, ymin=0, legend pos=outer north east")

In [ ]:
# problem.constraints += uy >= cos(θ) * σ
Axis(
    [
        Plots.Linear(t, (u2 ./ σ) , style="solid, thick, blue, mark=none", legendentry="thrust angle"),
        Plots.Linear([t[1], t[n]], [cos(θ), cos(θ)], style="solid, thick, black, mark=none", legendentry="cos sigma")
     ], xlabel="time [s]", style="width=15cm, height=8cm")

In [ ]:
Axis(
    Plots.Linear(t, rad2deg.(thrust_ang), style="solid, thick, blue, mark=none"),
     xlabel="time [s]", ylabel="thrust angle [deg]", style="width=15cm, height=8cm")

In [ ]:
Axis([
        Plots.Linear(t, xs, style="solid, ultra thick, blue, mark=none", legendentry="x [m]"),
        Plots.Linear(t, ys, style="solid, ultra thick, red, mark=none", legendentry="y [m]"),
        Plots.Linear(t, us, style="solid, ultra thick, green, mark=none", legendentry="u [m/s]"),
        Plots.Linear(t, vs, style="solid, ultra thick, orange, mark=none", legendentry="v [m/s]")
     ], xlabel="time [s]", ylabel="state", style="width=15cm, enlarge x limits=0")

In [ ]:
x_min, x_max = extrema(xs)
no_fly_pts = [x_min-100.0, 0.0, x_max+100.0]

Axis(
     [
        Plots.Scatter(xs, ys, style="solid, black, mark=*"),
        Plots.Linear(no_fly_pts, [abs(x)*sin(γ) for x in no_fly_pts], style="solid, gray, mark=none"),
        Plots.Linear(no_fly_pts, [0.0 for x in no_fly_pts], style="solid, black, mark=none")
     ], xlabel="x [m]", ylabel="y [m]", style="width=20cm, enlarge x limits=0")